# Loading and displaying incons form the prepared csv files in a map.

In [94]:
import pathlib
import glob
import pandas as pd

from collections import defaultdict

import folium
from folium import Map, LayerControl
from folium.plugins import MarkerCluster

from folium.raster_layers import TileLayer
from folium.plugins import FloatImage
from folium import plugins
from folium.features import CustomIcon
from folium import IFrame
import branca

import base64


In [102]:
path = r'data\asia\asia_countries'
# get all filenames under the data directory
l = [pd.read_csv(filename, encoding='utf') for filename in glob.glob(path + "/*.csv")]

# check the list size to understand how many files will be read
print(len(l))

#  create the dataset using all files under the data directory
df = pd.concat(l, axis=0)
#df.drop(['source','Unnamed: 10','Unnamed: 11'], axis=1, inplace=True)
df['latitude'] = df['latitude'].astype(float)
df['longitude'] = df['longitude'].astype(float)
df['build_year'] = df['build_year'].astype(str)
#df.dropna(axis=0 , inplace=True)
df.reset_index(inplace=True,drop=True)
# df.head(50)

18


Popup table function

In [103]:
def popup_html_table(row):
  """
  Function that extracts the information from each row of the dataframe and
  creates an html table with that information inside. This is the first part of the html for the pop up box.
  """
  #print(row)

  country = str(row['country'])
  name = row['name']
  build_year = row['build_year']
  religion = row['religion']
  remakrs = row['remakrs']
  sources = row['sources']

  img_name = df['img_name']

  #left_col_color = "#3e95b5"
  left_col_color = '#6E6C70'
  right_col_color = "#D4DCFF"


  html = """
        <!DOCTYPE html>
        <html dir = 'rtl' lang = 'fa'>
        <html>


        <center><h2 style="margin-bottom:5"; width="500px">{}</h2>""".format(name) + """</center>
        <center> <table style="height: 126px; width: 500px;">

        <tbody>
        <tr>
        <td style="background-color: """+ left_col_color +""";"><span style="color: #ffffff;"> کشور </span></td>
        <td style="width: 400px;background-color: """+ right_col_color +""";">"""+ country + """</td>
        </tr>

        <tr>
        <td style="background-color: """+ left_col_color +""";"><span style="color: #ffffff;"> سال ساخت </span></td>
        <td style="width: 400px;background-color: """+ right_col_color +""";">"""+build_year + """</td>
        </tr>

        <tr>
        <td style="background-color: """+ left_col_color +""";"><span style="color: #ffffff;"> دین </span></td>
        <td style="width: 400px;background-color: """+ right_col_color +""";">"""+religion + """</td>
        </tr>

        <tr>
        <td style="background-color: """+ left_col_color +""";"><span style="color: #ffffff;"> توضیحات </span></td>
        <td style="width: 400px;background-color: """+ right_col_color +""";">"""+remakrs + """</td>
        </tr>

        <tr>
        <td style="background-color: """+ left_col_color +""";"><span style="color: #ffffff;"> منابع </span></td>
        <td style="width: 400px;background-color: """+ right_col_color +""";">"""+sources + """</td>
        </tr>
        </tr>

        </tbody>
        </table></center>



        </html>
"""
  return html

In [104]:
# popup_frame and image

def mapper(df):

  # tiles = 'https://server.arcgisonline.com/ArcGIS/rest/services/NatGeo_World_Map/MapServer/tile/{z}/{y}/{x}'
  # attr = 'Tiles &copy; Esri &mdash; National Geographic, Esri, DeLorme, NAVTEQ, UNEP-WCMC, USGS, NASA, ESA, METI, NRCAN, GEBCO, NOAA, iPC'
  # map = folium.Map(location=(40, 55), zoom_start=3, tiles=tiles, attr = attr, control_scale=True, scrollWheelZoom=True, dragging=True)


  map = folium.Map(location=(40, 55), zoom_start=4, control_scale=True, scrollWheelZoom=True, dragging=True)

  #map = folium.Map(location=(40, 55), tiles = 'Stamen Toner', zoom_start=5, control_scale=True, scrollWheelZoom=True, dragging=True)

  # Default dictionary
  icon_dict = defaultdict(list)
  icon_dict ["اسلام"] = "star-and-crescent"
  icon_dict ["مسیحیت"] = "cross"
  icon_dict["یهودیت"] = "star-of-david"


  # Adding Marker CLusters for layer control
  mCluster = {}

  for e in df.country.unique():
    mCluster[e] = MarkerCluster(name = e)#.add_to(map)

  # main loop
  for i, row in df.iterrows():
    #print(row['name'])
    Filename = path+'/asia_img/'+row['img_name']
    encoded = base64.b64encode(open(Filename, 'rb').read())
    svg = """
    <center><object data="data:image/jpg;base64,{}" width="{}" height="{} type="image/svg+xml">
    </object></center>""".format

    # Getting the first html part with the table and title
    
    my_html = popup_html_table(row)

    width, height, fat_wh = 500, 300, 1.1

    # Adding the encoded image
    html = my_html + svg(encoded.decode('UTF-8'), width, height)

    # constructing the frame
    iframe = branca.element.IFrame(html , width=width*fat_wh, height=height*fat_wh)
    popup  = folium.Popup(iframe, parse_html = True, max_width=600)

    # making the marker
    marker = folium.Marker(location=[row['latitude'], row['longitude']],popup=popup,
                  icon=folium.Icon(icon=icon_dict[row['religion']], prefix='fa', color = 'red'))

    mCluster[row['country']].add_child(marker).add_to(map)

  folium.LayerControl().add_to(map)

  return map

map = mapper(df)

In [105]:
map
map.save(outfile= "data/Created_Maps/map_asia.html")

Working on the supplied data

In [106]:
map